In [1]:
import backtrader as bt
import pandas as pd
from statsmodels.tsa.statespace.sarimax import SARIMAX
import logging
import requests
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from polygon import StocksClient 
import logging


In [2]:
API_KEY = "uwQtl3txGt5BLbecq7ZbIu0ZbuitCGjc"

In [3]:
async def get_GLD(plot=False):
    try:
        logging.info("Initializing StocksClient...")
        async_stock_client = StocksClient(API_KEY, True)

        logging.info("Fetching aggregate bars data for 'GLD'...")
        response = await async_stock_client.get_aggregate_bars(
            'GLD',
            '2010-01-01',
            '2024-09-01',
            full_range=True
        )

        if not response:
            logging.error("Received empty response from StocksClient.")
            return None

        logging.info("Converting response to DataFrame...")
        df = pd.DataFrame(response)

        if 't' not in df.columns:
            logging.error("Expected column 't' not found in response.")
            return None

        logging.info(
            "Converting 't' column to datetime and setting as index...")
        df['Date'] = pd.to_datetime(df['t'], unit='ms')
        df.set_index('Date', inplace=True)
        df.drop(columns=['t'], inplace=True)

        logging.info("Renaming columns...")
        df.rename(columns={
            'o': 'Open',
            'h': 'High',
            'l': 'Low',
            'c': 'Close',
            'v': 'Volume',
            'n': 'Transactions'
        }, inplace=True)

        logging.info("Selecting relevant columns...")
        df = df[['Open', 'High', 'Low', 'Close', 'Volume']]

        logging.info("Converting columns to numeric types...")
        numeric_columns = ['Open', 'High', 'Low', 'Close', 'Volume']
        df[numeric_columns] = df[numeric_columns].apply(
            pd.to_numeric, errors='coerce')

        if plot:
            logging.info("Plotting close prices...")
            plt.figure(figsize=(14, 7))
            plt.plot(df.index, df['Close'], label='Close Price', color='blue')
            plt.title('GLD Close Prices (2010-01-01 to 2024-09-01)')
            plt.xlabel('Date')
            plt.ylabel('Price')
            plt.legend()
            plt.grid(True)
            plt.tight_layout()
            plt.show()

        csv_filename = 'GLD-Prices.csv'
        df.to_csv(csv_filename, index=True)
        logging.info(f"GLD prices saved to '{csv_filename}'.")

    except Exception as e:
        logging.error(f"An error occurred in get_GLD: {e}")
        return None
    return df


async def get_SLV(plot=False):
    try:
        logging.info("Initializing StocksClient...")
        async_stock_client = StocksClient(API_KEY, True)

        logging.info("Fetching aggregate bars data for 'SLV'...")
        response = await async_stock_client.get_aggregate_bars(
            'SLV',
            '2010-01-01',
            '2024-09-01',
            full_range=True
        )

        if not response:
            logging.error("Received empty response from StocksClient.")
            return None

        logging.info("Converting response to DataFrame...")
        df = pd.DataFrame(response)

        if 't' not in df.columns:
            logging.error("Expected column 't' not found in response.")
            return None

        logging.info(
            "Converting 't' column to datetime and setting as index...")
        df['Date'] = pd.to_datetime(df['t'], unit='ms')
        df.set_index('Date', inplace=True)
        df.drop(columns=['t'], inplace=True)

        logging.info("Renaming columns...")
        df.rename(columns={
            'o': 'Open',
            'h': 'High',
            'l': 'Low',
            'c': 'Close',
            'v': 'Volume',
            'n': 'Transactions'
        }, inplace=True)

        logging.info("Selecting relevant columns...")
        df = df[['Open', 'High', 'Low', 'Close', 'Volume']]

        logging.info("Converting columns to numeric types...")
        numeric_columns = ['Open', 'High', 'Low', 'Close', 'Volume']
        df[numeric_columns] = df[numeric_columns].apply(
            pd.to_numeric, errors='coerce')

        if plot:
            logging.info("Plotting close prices...")
            plt.figure(figsize=(14, 7))
            plt.plot(df.index, df['Close'], label='Close Price', color='blue')
            plt.title('SLV Close Prices (2010-01-01 to 2024-09-01)')
            plt.xlabel('Date')
            plt.ylabel('Price')
            plt.legend()
            plt.grid(True)
            plt.tight_layout()
            plt.show()

        csv_filename = 'SLV-Prices.csv'
        df.to_csv(csv_filename, index=True)
        logging.info(f"SLV prices saved to '{csv_filename}'.")

    except Exception as e:
        logging.error(f"An error occurred in get_SLV: {e}")
        return None
    return df

gld_data = await get_GLD()
slv_data = await get_SLV()

In [16]:

def fetch_polygon_data(ticker, timespan='day', from_date='2020-01-01', to_date='2023-12-31', api_key='YOUR_POLYGON_API_KEY'):
    """
    Fetches historical data from Polygon.io.

    Parameters:
        ticker (str): Stock ticker symbol (e.g., 'GLD', 'SLV').
        timespan (str): Timespan of the data (e.g., 'minute', 'hour', 'day').
        from_date (str): Start date in 'YYYY-MM-DD' format.
        to_date (str): End date in 'YYYY-MM-DD' format.
        api_key (str): Your Polygon.io API key.

    Returns:
        pd.DataFrame: DataFrame containing historical data.
    """
    url = f'https://api.polygon.io/v2/aggs/ticker/{ticker}/range/1/{timespan}/{from_date}/{to_date}'
    params = {
        'adjusted': 'true',
        'sort': 'asc',
        'limit': 50000,  # Maximum number of results per request
        'apiKey': api_key
    }

    try:
        response = requests.get(url, params=params)
        response.raise_for_status()
        data = response.json()

        if 'results' not in data:
            logging.error(
                f"No results found for ticker {ticker}. Response: {data}")
            return None

        df = pd.DataFrame(data['results'])
        # Convert timestamp to datetime
        df['t'] = pd.to_datetime(df['t'], unit='ms')
        df.set_index('t', inplace=True)
        df.rename(columns={
            'o': 'Open',
            'h': 'High',
            'l': 'Low',
            'c': 'Close',
            'v': 'Volume',
            'n': 'Transactions'
        }, inplace=True)
        return df[['Open', 'High', 'Low', 'Close', 'Volume']]

    except requests.exceptions.HTTPError as http_err:
        logging.error(f"HTTP error occurred for ticker {ticker}: {http_err}")
    except Exception as err:
        logging.error(f"An error occurred for ticker {ticker}: {err}")

    return None


# Example usage:
# Replace 'YOUR_POLYGON_API_KEY' with your actual API key
gld_data = fetch_polygon_data(
    'GLD', from_date='2020-01-01', to_date='2023-12-31', api_key='YOUR_POLYGON_API_KEY')
slv_data = fetch_polygon_data(
    'SLV', from_date='2020-01-01', to_date='2023-12-31', api_key='YOUR_POLYGON_API_KEY')

# Check if data fetching was successful
if gld_data is None or slv_data is None:
    logging.error("Data fetching failed. Exiting the script.")
    exit()

ERROR:root:HTTP error occurred for ticker GLD: 401 Client Error: Unauthorized for url: https://api.polygon.io/v2/aggs/ticker/GLD/range/1/day/2020-01-01/2023-12-31?adjusted=true&sort=asc&limit=50000&apiKey=YOUR_POLYGON_API_KEY
ERROR:root:HTTP error occurred for ticker SLV: 401 Client Error: Unauthorized for url: https://api.polygon.io/v2/aggs/ticker/SLV/range/1/day/2020-01-01/2023-12-31?adjusted=true&sort=asc&limit=50000&apiKey=YOUR_POLYGON_API_KEY
ERROR:root:Data fetching failed. Exiting the script.


In [5]:

class PandasData(bt.feeds.PandasData):
    """
    Customized Pandas Data Feed for Backtrader.
    """
    params = (
        ('datetime', None),  # Use the DataFrame index as datetime
        ('open', 'Open'),
        ('high', 'High'),
        ('low', 'Low'),
        ('close', 'Close'),
        ('volume', 'Volume'),
        ('openinterest', -1),  # No open interest data
    )


# Create data feeds for GLD and SLV
data_gld = PandasData(dataname=gld_data)
data_slv = PandasData(dataname=slv_data)

In [8]:
class SARIMAXStrategy(bt.Strategy):
    params = (
        ('forecast_period', 1),          # Number of days to forecast ahead
        ('model_order', (1, 1, 1)),      # SARIMAX (p,d,q) order
        ('seasonal_order', (1, 1, 1, 7)),  # SARIMAX (P,D,Q,s) seasonal order
        ('threshold', 0.5),              # Threshold for making trades
        ('verbose', False),              # Enable detailed logging
        ('min_data_points', 30),         # Minimum data points required to fit the model
    )

    def __init__(self):
        # Reference to the close prices
        self.dataclose = self.datas[0].close

        # Initialize variables to track orders
        self.order = None

        # Model variables
        self.model = None
        self.model_fit = None

    def next(self):
        """
        Called for each new data point. Make predictions and execute trades.
        """
        if self.order:
            # Pending order execution
            return

        # Ensure we have enough data to fit the model
        if len(self.dataclose) < self.params.min_data_points:
            return

        # Extract historical close prices
        historical_data = pd.Series(
            [self.dataclose[-i] for i in range(self.params.min_data_points, 0, -1)]
        )

        # Convert to numeric and drop NaNs
        historical_data = pd.to_numeric(historical_data, errors='coerce').dropna()

        try:
            # Initialize and fit the SARIMAX model
            self.model = SARIMAX(
                historical_data,
                order=self.params.model_order,
                seasonal_order=self.params.seasonal_order,
                enforce_stationarity=False,
                enforce_invertibility=False
            )
            self.model_fit = self.model.fit(disp=False)

            if self.params.verbose:
                print(self.model_fit.summary())

            # Make a forecast
            forecast = self.model_fit.forecast(steps=self.params.forecast_period)
            predicted_price = forecast.iloc[-1]

            # Current price
            current_price = self.dataclose[0]

            if self.params.verbose:
                print(f"Predicted Price: {predicted_price}, Current Price: {current_price}")

            # Trading logic based on prediction
            if predicted_price > current_price + self.params.threshold:
                # Buy signal
                if not self.position:
                    self.order = self.buy()
                    if self.params.verbose:
                        print(f"BUY EXECUTED at {current_price}")
            elif predicted_price < current_price - self.params.threshold:
                # Sell signal
                if self.position:
                    self.order = self.sell()
                    if self.params.verbose:
                        print(f"SELL EXECUTED at {current_price}")

        except Exception as e:
            logging.error(f"Error during forecasting and trading: {e}")

    def notify_order(self, order):
        """
        Notification for order status changes.
        """
        if order.status in [order.Submitted, order.Accepted]:
            # Order submitted/accepted, nothing to do
            return

        if order.status in [order.Completed]:
            if order.isbuy():
                self.buyprice = order.executed.price
                self.buycomm = order.executed.comm
                if self.params.verbose:
                    print(f"BUY ORDER COMPLETED at {self.buyprice}")
            elif order.issell():
                if self.params.verbose:
                    print(f"SELL ORDER COMPLETED at {order.executed.price}")

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            logging.warning(f"Order {order.Status[order.status]}")

        # Reset orders
        self.order = None

    def notify_trade(self, trade):
        """
        Notification for trade status changes.
        """
        if not trade.isclosed:
            return

        if self.params.verbose:
            print(f"OPERATION PROFIT, GROSS {trade.pnl}, NET {trade.pnlcomm}")


In [11]:
# Initialize Cerebro engine
cerebro = bt.Cerebro()

# Add data feeds to Cerebro
cerebro.adddata(data_gld, name='GLD')
# Uncomment the next line if you wish to add SLV data
# cerebro.adddata(data_slv, name='SLV')

# Add the SARIMAX strategy to Cerebro
cerebro.addstrategy(
    SARIMAXStrategy,
    forecast_period=1,
    model_order=(1, 1, 1),
    seasonal_order=(1, 1, 1, 7),
    threshold=0.5,
    verbose=True  # Set to True for detailed logging
)

# Set initial capital
cerebro.broker.setcash(100000.0)

# Set commission - 0.1% per trade
cerebro.broker.setcommission(commission=0.001)

# Print starting portfolio value
print(f"Starting Portfolio Value: {cerebro.broker.getvalue():.2f}")

# Run the backtest
results = cerebro.run()

# Print final portfolio value
print(f"Final Portfolio Value: {cerebro.broker.getvalue():.2f}")

# Plot the results
cerebro.plot(style='candlestick')

Starting Portfolio Value: 100000.00
                                     SARIMAX Results                                     
Dep. Variable:                                 y   No. Observations:                   30
Model:             SARIMAX(1, 1, 1)x(1, 1, 1, 7)   Log Likelihood                 -26.492
Date:                           Wed, 09 Oct 2024   AIC                             62.984
Time:                                   14:39:34   BIC                             65.809
Sample:                                        0   HQIC                            62.404
                                            - 30                                         
Covariance Type:                             opg                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
ar.L1         -0.3505      1.832     -0.191      0.848      -3.942       3.241
ma.L1  

/Users/amv10802/Documents/Quant IC/sarima_forecast/sarima_forecast/lib/python3.10/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/amv10802/Documents/Quant IC/sarima_forecast/sarima_forecast/lib/python3.10/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "


                                     SARIMAX Results                                     
Dep. Variable:                                 y   No. Observations:                   30
Model:             SARIMAX(1, 1, 1)x(1, 1, 1, 7)   Log Likelihood                 -26.906
Date:                           Wed, 09 Oct 2024   AIC                             63.812
Time:                                   14:39:34   BIC                             66.637
Sample:                                        0   HQIC                            63.232
                                            - 30                                         
Covariance Type:                             opg                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
ar.L1         -0.8495      0.788     -1.078      0.281      -2.394       0.695
ma.L1          1.5005      2.341      0.641

/Users/amv10802/Documents/Quant IC/sarima_forecast/sarima_forecast/lib/python3.10/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "


                                     SARIMAX Results                                     
Dep. Variable:                                 y   No. Observations:                   30
Model:             SARIMAX(1, 1, 1)x(1, 1, 1, 7)   Log Likelihood                 -22.202
Date:                           Wed, 09 Oct 2024   AIC                             54.404
Time:                                   14:39:34   BIC                             57.229
Sample:                                        0   HQIC                            53.824
                                            - 30                                         
Covariance Type:                             opg                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
ar.L1         -0.5624      0.483     -1.165      0.244      -1.508       0.383
ma.L1          1.0000   3.23e+04    3.1e-05

...

                                     SARIMAX Results                                     
Dep. Variable:                                 y   No. Observations:                   30
Model:             SARIMAX(1, 1, 1)x(1, 1, 1, 7)   Log Likelihood                 -32.273
Date:                           Wed, 09 Oct 2024   AIC                             74.545
Time:                                   14:42:02   BIC                             77.370
Sample:                                        0   HQIC                            73.965
                                            - 30                                         
Covariance Type:                             opg                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
ar.L1          0.4531      0.319      1.419      0.156      -0.173       1.079
ma.L1         -0.7928      0.449     -1.764

/Users/amv10802/Documents/Quant IC/sarima_forecast/sarima_forecast/lib/python3.10/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/amv10802/Documents/Quant IC/sarima_forecast/sarima_forecast/lib/python3.10/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/amv10802/Documents/Quant IC/sarima_forecast/sarima_forecast/lib/python3.10/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "


                                     SARIMAX Results                                     
Dep. Variable:                                 y   No. Observations:                   30
Model:             SARIMAX(1, 1, 1)x(1, 1, 1, 7)   Log Likelihood                 -30.189
Date:                           Wed, 09 Oct 2024   AIC                             70.378
Time:                                   14:42:03   BIC                             73.203
Sample:                                        0   HQIC                            69.798
                                            - 30                                         
Covariance Type:                             opg                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
ar.L1         -1.1332      0.201     -5.649      0.000      -1.526      -0.740
ma.L1          1.0000   6882.332      0.000

<IPython.core.display.Javascript object>

[[<Figure size 640x480 with 4 Axes>]]